In [1]:
import os
import pandas as pd
import torch
import torch.nn as nn
import torchvision
import torchvision.transforms as transforms
import torchmetrics
import pickle
from torch.utils.data import Dataset, DataLoader
from PIL import Image
import lightning as pl

/opt/miniconda3/envs/real-estate-analysis-torch/lib/python3.11/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: 'dlopen(/opt/miniconda3/envs/real-estate-analysis-torch/lib/python3.11/site-packages/torchvision/image.so, 0x0006): Symbol not found: __ZN3c1017RegisterOperatorsD1Ev
  Referenced from: <CFED5F8E-EC3F-36FD-AAA3-2C6C7F8D3DD9> /opt/miniconda3/envs/real-estate-analysis-torch/lib/python3.11/site-packages/torchvision/image.so
  Expected in:     <761A4B43-4CD1-322C-BB16-CEE783FE0A7C> /opt/miniconda3/envs/real-estate-analysis-torch/lib/python3.11/site-packages/torch/lib/libtorch_cpu.dylib'If you don't plan on using image functionality from `torchvision.io`, you can ignore this warning. Otherwise, there might be something wrong with your environment. Did you have `libjpeg` or `libpng` installed before building `torchvision` from source?
  warn(


In [2]:
df = pd.read_pickle('./data/flats_train.pkl')
df

Numer oferty Liczba pokoi Piętro Liczba pięter  Powierzchnia  \
0   28111/3685/OMS            2      2             4         47.88   
1   28902/3685/OMS            2      4             4         43.20   
2   28987/3685/OMS            2      4             6         32.75   
3   26218/3685/OMS            3      4             4         68.50   
4   31133/3685/OMS            2      1             4         41.81   
..             ...          ...    ...           ...           ...   
87  22101/3685/OMS            5      0             2        125.09   
88  28798/3685/OMS            4      6             7        103.38   
89  27282/3685/OMS            1      0             4         32.04   
91  26784/3685/OMS            2      5             6         36.82   
92  25484/3685/OMS            4      2             3        131.88   

    Czynsz administracyjny  Stan nieruchomości  Umeblowanie  Rodzaj budynku  \
0                   930.00                   9            3               2   
1                   710.00                   5            0               8   
2                   290.00                   9            3               2   
3                   770.00                   8           -1               8   
4                   544.25                   0           -1               8   
..                     ...                 ...          ...             ...   
87                    0.00                  11            2               9   
88                 1342.00                   0            0               0   
89                  504.99                   8            3               5   
91                  250.00                   9            3               8   
92                  959.03                   8           -1               6   

    Rok budowy  ...  Typ_mieszkania_Jednopoziomowe  Balkon  Alarm  Monitoring  \
0       2017.0  ...                          False       1      0           1   
1       1965.0  ...                          False       1      0           0   
2       2022.0  ...                          False       1      0           1   
3       1970.0  ...                          False       1      0           0   
4       2012.0  ...                           True       1      0           1   
..         ...  ...                            ...     ...    ...         ...   
87      2024.0  ...                          False       1      0           0   
88      2001.0  ...                          False       1      0           0   
89      2009.0  ...                           True       1      0           1   
91      2022.0  ...                           True       1      0           1   
92      1930.0  ...                          False       1      0           0   

    Ochrona  Recepcja  Teren ogrodzony  Liczba oddzielnych toalet      Cena  \
0         1         1                1                          0  756000.0   
1         0         0                0                          0  400000.0   
2         0         0                1                          0  475000.0   
3         0         0                0                          2  475000.0   
4         0         0                1                          0  550000.0   
..      ...       ...              ...                        ...       ...   
87        0         0                1                          0  990000.0   
88        0         0                0                          0  950000.0   
89        0         0                0                          0  352440.0   
91        0         0                0                          0  620000.0   
92        0         0                0                          0  930000.0   

    Cena za m2  
0      15789.0  
1       9259.0  
2      14504.0  
3       6934.0  
4      13155.0  
..         ...  
87      7914.0  
88      9189.0  
89     11000.0  
91     16839.0  
92      7052.0  

[81 rows x 76 columns]

In [3]:
device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps"
    if torch.backends.mps.is_available()
    else "cpu"
)
print(f"Using {device} device")

Using mps device


In [4]:
# dinov2_vits14 = torch.hub.load(
#     "facebookresearch/dinov2", "dinov2_vits14_reg").to(device)


class CustomDataset(Dataset):
    def __init__(self, df, transform=None):
        self.df = df
        self.transform = transform

    def __len__(self):
        return len(self.df)

    def get_photos(self, offer_id):
        batch = []
        for root, _, files in os.walk(f"./images/{offer_id}"):
            for file in files:
                if file.endswith(".jpg") and "all" not in file and "wp" not in file:
                    image_path = os.path.join(root, file)
                    image = Image.open(image_path).convert("RGB")

                    if self.transform:
                        image = self.transform(image)
                    else:
                        image = transforms.ToTensor()(image)

                    batch.append(image)

        if len(batch) == 0:
            return None

        return torch.stack(batch)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]

        offer_id = row['Numer oferty']
        # photos = self.get_photos(offer_id)

        features = row.iloc[1:-2].astype(float)
        features = torch.tensor(features, dtype=torch.float32)

        target = row.iloc[-2:].astype(float)
        target = torch.tensor(target, dtype=torch.float32)

        return offer_id, features, target


transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406],
                         std=[0.229, 0.224, 0.225]),
])

dataset = CustomDataset(df, transform)
dataloader = DataLoader(dataset, batch_size=1, shuffle=True)

In [5]:
class LinearClassifierHead(nn.Module):
    def __init__(self, embed_dim, num_classes):
        super().__init__()
        self.head = nn.Linear(embed_dim, num_classes)

    def forward(self, x):
        return self.head(x)


class CustomModel(pl.LightningModule):
    def __init__(self, learning_rate):
        super().__init__()
        self.linear_classifier_head = LinearClassifierHead(457, 2)
        self.criterion = nn.MSELoss(reduction='none')
        self.rmse = torchmetrics.MeanSquaredError()
        self.learning_rate = learning_rate

    def configure_optimizers(self):
        optimizer = torch.optim.Adam(
            self.linear_classifier_head.parameters(), lr=self.learning_rate)
        return optimizer

    def read_embeddings(self, offers_id):
        batch_embeddings = []
        for offer_id in offers_id:
            embedded_filename = '_'.join(offer_id.split("/"))

            with open(f"./images_embeded/{embedded_filename}.pkl", 'rb') as f:
                embedding = pickle.load(f)['outputs']

            batch_embeddings.append(torch.tensor(
                embedding, dtype=torch.float32))
        return torch.stack(batch_embeddings)

    def forward(self, offer_id, features):
        embeded_photos = self.read_embeddings(offer_id).to(device)
        embeded_photos = embeded_photos.mean(axis=1)

        merged = torch.cat((embeded_photos, features), dim=1)

        return self.linear_classifier_head(merged)

    def training_step(self, batch, batch_idx):
        offer_id, features, target = batch

        outputs = self(offer_id, features)

        loss = self.criterion(outputs, target)
        rmse = self.rmse(outputs, target)

        self.log_dict({
            'train_loss_price': loss[0][0],
            'train_loss_price_per_m2': loss[0][1],
            'train_rmse': rmse
        })
        return loss[0][0]

    def test_step(self, batch, batch_idx):
        offer_id, features, target = batch

        outputs = self(offer_id, features)

        loss = self.criterion(outputs, target)
        rmse = self.rmse(outputs, target)

        self.log_dict({
            'test_loss_price': loss[0][0],
            'test_loss_price_per_m2': loss[0][1],
            'test_rmse': rmse
        })

In [6]:
model = CustomModel(learning_rate=1e-3)
trainer = pl.Trainer(max_epochs=100)

trainer.fit(model, train_dataloaders=dataloader)

GPU available: True (mps), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
/opt/miniconda3/envs/real-estate-analysis-torch/lib/python3.11/site-packages/lightning/pytorch/trainer/connectors/logger_connector/logger_connector.py:67: UserWarning: Starting from v1.9.0, `tensorboardX` has been removed as a dependency of the `lightning.pytorch` package, due to potential conflicts with other packages in the ML ecosystem. For this reason, `logger=True` will use `CSVLogger` as the default logger, unless the `tensorboard` or `tensorboardX` packages are found. Please `pip install lightning[extra]` or one of them to enable TensorBoard support by default
  warning_cache.warn(

  | Name                   | Type                 | Params
----------------------------------------------------------------
0 | linear_classifier_head | LinearClassifierHead | 916   
1 | criterion              | MSELoss              | 0     
2 | rmse  

Epoch 0:   0%|          | 0/81 [00:00<?, ?it/s] 

/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  features = torch.tensor(features, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:43: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  target = torch.tensor(target, dtype=torch.float32)


Epoch 0:   2%|▏         | 2/81 [00:00<00:07, 10.16it/s, v_num=37]

/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  features = torch.tensor(features, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:43: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  target = torch.tensor(target, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior).

...

Epoch 99:  89%|████████▉ | 72/81 [00:00<00:00, 201.81it/s, v_num=37]

/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  features = torch.tensor(features, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:43: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  target = torch.tensor(target, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior).

Epoch 99: 100%|██████████| 81/81 [00:00<00:00, 205.15it/s, v_num=37]

/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  features = torch.tensor(features, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:43: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  target = torch.tensor(target, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior).

Epoch 99: 100%|██████████| 81/81 [00:00<00:00, 203.69it/s, v_num=37]


In [7]:
offer_id, features, target = next(iter(dataloader))

features = features.to(device)
target = target.to(device)

model = model.to(device)
output = model(offer_id, features)

/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:40: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  features = torch.tensor(features, dtype=torch.float32)
/var/folders/_s/r6q44yzn7gd7hjnfjjlpb4hm0000gn/T/ipykernel_9250/3767603427.py:43: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  target = torch.tensor(target, dtype=torch.float32)


In [8]:
output, target

(tensor([[21486.9453,    36.4979]], device='mps:0', grad_fn=<LinearBackward0>),
 tensor([[799000.,  16474.]], device='mps:0'))

In [9]:
import numpy as np
np.sqrt(nn.MSELoss(reduction='none')(output, target).detach().cpu().numpy())

array([[777513.06 ,  16437.502]], dtype=float32)